In [1]:
!nvidia-smi -L

GPU 0: Tesla V100-SXM3-32GB (UUID: GPU-ec1762f7-8403-9c77-05dc-2d847fd802e4)


Prepare the environment.

In [3]:
!pip install git+https://github.com/openai/jukebox.git

  Cloning https://github.com/openai/jukebox.git to /tmp/pip-req-build-l4j_1oyp
  Running command git clone -q https://github.com/openai/jukebox.git /tmp/pip-req-build-l4j_1oyp
  Using cached fire-0.1.3-py2.py3-none-any.whl
  Using cached tqdm-4.45.0-py2.py3-none-any.whl (60 kB)
  Using cached Unidecode-1.1.1-py2.py3-none-any.whl (238 kB)
  Using cached numba-0.48.0-1-cp37-cp37m-manylinux2014_x86_64.whl (3.5 MB)
  Using cached librosa-0.7.2-py3-none-any.whl
  Using cached llvmlite-0.31.0-cp37-cp37m-manylinux1_x86_64.whl (20.2 MB)
  Created wheel for jukebox: filename=jukebox-1.0-py3-none-any.whl size=191319 sha256=f8bc2a15ef79a88f2986afc073d98bf283e4a924f30ddcc2fbfb35fb92c3b302
  Stored in directory: /tmp/pip-ephem-wheel-cache-1ddrc7mq/wheels/d6/42/39/91f8a32505a445499702ae0f887769e6bb5030c42382d74ae0
Successfully built jukebox
  Attempting uninstall: llvmlite
    Found existing installation: llvmlite 0.36.0
    Uninstalling llvmlite-0.36.0:
      Successfully uninstalled llvmlite-0.36.

In [4]:
import jukebox
import torch as t
import librosa
import os
from IPython.display import Audio
from jukebox.make_models import make_vqvae, make_prior, MODELS, make_model
from jukebox.hparams import Hyperparams, setup_hparams
from jukebox.sample import sample_single_window, _sample, \
                           sample_partial_window, upsample, \
                           load_prompts
from jukebox.utils.dist_utils import setup_dist_from_mpi
from jukebox.utils.torch_utils import empty_cache
rank, local_rank, device = setup_dist_from_mpi()

Using cuda True


# Генерация музыки с помощью 1b/5b моделей в Jukebox


In [5]:
model = '1b_lyrics' # '5b_lyrics' or '5b' -- выберите одну из моделей, 1b менее требовательная
                    # но у 5b лучше качество
hps = Hyperparams()
hps.sr = 44100
hps.n_samples = 3 if model in ('5b', '5b_lyrics') else 8
hps.name = 'test_1b'# укажите название данной генерации
chunk_size = 16 if model in ('5b', '5b_lyrics') else 32
max_batch_size = 3 if model in ('5b', '5b_lyrics') else 16
hps.levels = 3
hps.hop_fraction = [.5,.5,.125]

vqvae, *priors = MODELS[model]
vqvae = make_vqvae(setup_hparams(vqvae, dict(sample_length = 1048576)), device)
top_prior = make_prior(setup_hparams(priors[-1], dict()), vqvae, device)

Restored from /home/jovyan/.cache/jukebox/models/5b/vqvae.pth.tar
0: Loading vqvae in eval mode
Using apex FusedLayerNorm
Creating cond. autoregress with prior bins [79, 2048], 
dims [384, 6144], 
shift [ 0 79]
input shape 6528
input bins 2127
Self copy is False
Loading artist IDs from /home/user/conda/lib/python3.7/site-packages/jukebox/data/ids/v3_artist_ids.txt
Loading artist IDs from /home/user/conda/lib/python3.7/site-packages/jukebox/data/ids/v3_genre_ids.txt
Level:2, Cond downsample:None, Raw to tokens:128, Sample length:786432
Running  wget -O /home/jovyan/.cache/jukebox/models/1b_lyrics/prior_level_2.pth.tar https://openaipublic.azureedge.net/jukebox/models/1b_lyrics/prior_level_2.pth.tar
Restored from /home/jovyan/.cache/jukebox/models/1b_lyrics/prior_level_2.pth.tar
0: Loading prior in eval mode


## Выберите режим генерации
Запустите одну из следующих ячеек. Первая отвечает за генерацию музыки с нуля, а вторая -- за генерацию продолжения для песни.

In [20]:
# В этом режиме мы будем генерировать песню с нуля, основываясь только на певце, жанре и тексте
mode = 'ancestral'
codes_file=None
audio_file=None
prompt_length_in_seconds=None

In [21]:
# А в этом -- возьмем за основу уже существующий трек, который вы выберете
mode = 'primed'
codes_file=None
# Тут укажите локальный путь до композиции, которую хотите продолжить
audio_file = "JukeboxTestWav/LittleBig-UNO.wav" 
# А тут укажите секунду, начиная с которой генерировать продолжение 
prompt_length_in_seconds=12 

Запустите данную ячейку, если хотите продолжить генерацию, которую останавливали ранее. Тогда предыдущие ячейки не будут иметь значения, режим будет выбран автоматически

In [8]:
if os.path.exists(hps.name):
  # Проверяем наличие 1/2 уровня генерации, чтобы начать с них, если что
  for level in [1, 2]:
    data = f"{hps.name}/level_{level}/data.pth.tar"
    if os.path.isfile(data):
      mode = 'upsample'
      codes_file = data
      print('Upsampling from level '+str(level))
      break
print('mode is now '+mode)

mode is now primed


Запустите данную ячейку, чтобы сохранить гиперпараметры

In [9]:
sample_hps = Hyperparams(dict(mode=mode, codes_file=codes_file, audio_file=audio_file, prompt_length_in_seconds=prompt_length_in_seconds))

Здесь вы можете уточнить ваш выбор певца, жанра и текста, на котором будет базироваться трек 

**ВАЖНО**: от длины композиции напрямую зависит время генерации (что логично), каждые 20 секунд генерации будут занимать 3 часа времени

In [10]:
sample_length_in_seconds = 20          # Здесь мы уточняем длину всей композиции
                                       # Для генерации с нуля лучше использовать значение в диапазоне 
                                       # от 1 до 4 минут
                                       # Также надо понимать, что модель генерирует музыку по-разному
                                       # В зависимости от того находится она в начале трека, в середине или в конце 
                
hps.sample_length = (int(sample_length_in_seconds*hps.sr)//top_prior.raw_to_tokens)*top_prior.raw_to_tokens
assert hps.sample_length >= top_prior.n_ctx*top_prior.raw_to_tokens, f'Please choose a larger sampling rate'

In [11]:
# Сейчас выбран певец Rick Astley, а жанр -- Pop
# Чтобы посмотреть полный доступный список жанров и певцов, перейдите по ссылке 
# https://github.com/openai/jukebox/tree/master/jukebox/data/ids
# Для 5b/5b_lyrics моделей все доступные варианты в наборе v2, для 1b/1b_lyrics в наборе v3

metas = [dict(artist = "Rick Astley",
            genre = "Pop",
            total_length = hps.sample_length,
            offset = 0,
            lyrics = """We're no strangers to love
You know the rules and so do I
A full commitment's what I'm thinking of
You wouldn't get this from any other guy

I just wanna tell you how I'm feeling
Gotta make you understand

Never gonna give you up
Never gonna let you down
Never gonna run around and desert you
Never gonna make you cry
Never gonna say goodbye
Never gonna tell a lie and hurt you

We've known each other for so long
Your heart's been aching, but
You're too shy to say it
Inside, we both know what's been going on
We know the game and we're gonna play it

And if you ask me how I'm feeling
Don't tell me you're too blind to see

Never gonna give you up
Never gonna let you down
Never gonna run around and desert you
Never gonna make you cry
Never gonna say goodbye
Never gonna tell a lie and hurt you

Never gonna give you up
Never gonna let you down
Never gonna run around and desert you
Never gonna make you cry
Never gonna say goodbye
Never gonna tell a lie and hurt you

(Ooh, give you up)
(Ooh, give you up)
Never gonna give, never gonna give
(Give you up)
Never gonna give, never gonna give
(Give you up)

We've known each other for so long
Your heart's been aching, but
You're too shy to say it
Inside, we both know what's been going on
We know the game and we're gonna play it

I just wanna tell you how I'm feeling
Gotta make you understand

Never gonna give you up
Never gonna let you down
Never gonna run around and desert you
Never gonna make you cry
Never gonna say goodbye
Never gonna tell a lie and hurt you

Never gonna give you up
Never gonna let you down
Never gonna run around and desert you
Never gonna make you cry
Never gonna say goodbye
Never gonna tell a lie and hurt you

Never gonna give you up
Never gonna let you down
Never gonna run around and desert you
Never gonna make you cry
Never gonna say goodbye
Never gonna tell a lie and hurt you
""",
            ),
          ] * hps.n_samples
labels = [None, None, top_prior.labeller.get_batch_labels(metas, 'cuda')]

Опционально настройте "температуру" сэмплирования. Авторы пишут, что значения .98 или .99 кажутся им оптимальными

In [12]:
sampling_temperature = .98

lower_batch_size = 16
max_batch_size = 3 if model in ('5b', '5b_lyrics') else 16
lower_level_chunk_size = 32
chunk_size = 16 if model in ('5b', '5b_lyrics') else 32
sampling_kwargs = [dict(temp=.99, fp16=True, max_batch_size=lower_batch_size,
                        chunk_size=lower_level_chunk_size),
                    dict(temp=0.99, fp16=True, max_batch_size=lower_batch_size,
                         chunk_size=lower_level_chunk_size),
                    dict(temp=sampling_temperature, fp16=True, 
                         max_batch_size=max_batch_size, chunk_size=chunk_size)]

Теперь мы готовы сэмплировать из модели. Мы сгенерим верхний уровень (2) сначала, потом средний уровень (1) и последний (0). 

После каждого из уровней мы декодируем в wav в формат и сохраняем в качестве аудио файлов. 

Генерация займет время, следующая ячейка будет выполняться около 10 минут на каждые 20 секунд генерируемой музыки
____

Если вам интересно более подробно ознакомиться с архитектурой модели и разобраться, почему сэмплирование происходит по уровням, то вы можете сделать это прочитав блог или статью

Ссылка на блог -- https://openai.com/blog/jukebox/

Ссылка на статью -- https://arxiv.org/abs/2005.00341

Ссылка на гитхаб -- https://github.com/openai/jukebox/

In [13]:
if sample_hps.mode == 'ancestral':
  zs = [t.zeros(hps.n_samples,0,dtype=t.long, device='cuda') for _ in range(len(priors))]
  zs = _sample(zs, labels, sampling_kwargs, [None, None, top_prior], [2], hps)
elif sample_hps.mode == 'upsample':
  assert sample_hps.codes_file is not None
  # Load codes.
  data = t.load(sample_hps.codes_file, map_location='cpu')
  zs = [z.cuda() for z in data['zs']]
  assert zs[-1].shape[0] == hps.n_samples, f"Expected bs = {hps.n_samples}, got {zs[-1].shape[0]}"
  del data
  print('Falling through to the upsample step later in the notebook.')
elif sample_hps.mode == 'primed':
  assert sample_hps.audio_file is not None
  audio_files = sample_hps.audio_file.split(',')
  duration = (int(sample_hps.prompt_length_in_seconds*hps.sr)//top_prior.raw_to_tokens)*top_prior.raw_to_tokens
  x = load_prompts(audio_files, duration, hps)
  zs = top_prior.encode(x, start_level=0, end_level=len(priors), bs_chunks=x.shape[0])
  zs = _sample(zs, labels, sampling_kwargs, [None, None, top_prior], [2], hps)
else:
  raise ValueError(f'Unknown sample mode {sample_hps.mode}.')

Sampling level 2
Sampling 6144 tokens for [0,6144]. Conditioning on 4134 tokens
Primed sampling 8 samples with temp=0.98, top_k=0, top_p=0.0
142/142 [00:13<00:00, 10.81it/s]
2010/2010 [02:04<00:00, 16.18it/s]
Sampling 6144 tokens for [746,6890]. Conditioning on 5398 tokens
Primed sampling 8 samples with temp=0.98, top_k=0, top_p=0.0
181/181 [00:16<00:00, 11.17it/s]
746/746 [00:45<00:00, 16.34it/s]


Теперь мы можем послушать первые результаты со 2 уровня! Заметьте, что это может быть довольно шумный звук -- так и должно быть, пока мы не пройдем следующие этапы генерации

In [14]:
Audio(f'{hps.name}/level_2/item_0.wav')

Так, мы сгенерировали верхний уровень, теперь займемся апсамплингом

In [15]:
if True:
  del top_prior
  empty_cache()
  top_prior=None
upsamplers = [make_prior(setup_hparams(prior, dict()), vqvae, 'cpu') for prior in priors[:-1]]
labels[:2] = [prior.labeller.get_batch_labels(metas, 'cuda') for prior in upsamplers]

Conditioning on 1 above level(s)
Checkpointing convs
Checkpointing convs
Loading artist IDs from /home/user/conda/lib/python3.7/site-packages/jukebox/data/ids/v2_artist_ids.txt
Loading artist IDs from /home/user/conda/lib/python3.7/site-packages/jukebox/data/ids/v2_genre_ids.txt
Level:0, Cond downsample:4, Raw to tokens:8, Sample length:65536
Running  wget -O /home/jovyan/.cache/jukebox/models/5b/prior_level_0.pth.tar https://openaipublic.azureedge.net/jukebox/models/5b/prior_level_0.pth.tar
Restored from /home/jovyan/.cache/jukebox/models/5b/prior_level_0.pth.tar
0: Loading prior in eval mode
Conditioning on 1 above level(s)
Checkpointing convs
Checkpointing convs
Loading artist IDs from /home/user/conda/lib/python3.7/site-packages/jukebox/data/ids/v2_artist_ids.txt
Loading artist IDs from /home/user/conda/lib/python3.7/site-packages/jukebox/data/ids/v2_genre_ids.txt
Level:1, Cond downsample:4, Raw to tokens:32, Sample length:262144
Running  wget -O /home/jovyan/.cache/jukebox/models/

Не пугайтесь: следующий шаг может занять несколько часов. Каждые 20 секунд генерации занимают порядка 3 часов на Nvidia Tesla V100. Level 1 -- это частично готовая генерация, а Level 0 -- уже финальный результат.

In [17]:
zs = upsample(zs, labels, sampling_kwargs, [*upsamplers, top_prior], hps)

Sampling level 1
Sampling 8192 tokens for [0,8192]. Conditioning on 8192 tokens
Sampling 8192 tokens for [4096,12288]. Conditioning on 8192 tokens
Sampling 8192 tokens for [8192,16384]. Conditioning on 8192 tokens
Sampling 8192 tokens for [12288,20480]. Conditioning on 4248 tokens
Primed sampling 8 samples with temp=0.99, top_k=0, top_p=0.0
133/133 [00:10<00:00, 12.90it/s]
3944/3944 [03:55<00:00, 16.76it/s]
Sampling 8192 tokens for [16384,24576]. Conditioning on 4096 tokens
Primed sampling 8 samples with temp=0.99, top_k=0, top_p=0.0
128/128 [00:09<00:00, 13.02it/s]
4096/4096 [04:08<00:00, 16.48it/s]
Sampling 8192 tokens for [19368,27560]. Conditioning on 5208 tokens
Primed sampling 8 samples with temp=0.99, top_k=0, top_p=0.0
163/163 [00:12<00:00, 12.80it/s]
2984/2984 [02:54<00:00, 17.14it/s]
Sampling level 0
Sampling 8192 tokens for [0,8192]. Conditioning on 8192 tokens
Sampling 8192 tokens for [4096,12288]. Conditioning on 8192 tokens
Sampling 8192 tokens for [8192,16384]. Condition

Теперь можете послушать то, что получилось!

In [18]:
Audio(f'{hps.name}/level_0/item_0.wav')

In [19]:
del upsamplers
empty_cache()